In [1]:
%%time
%reload_ext autoreload
%autoreload
%autoreload 2
%config Completer.use_jedi = False

import os
import json
import warnings
import pprint
import sys
import numpy as np
import pandas as pd
import torch

MAIN_PATH = os.getcwd().split("notebooks")[0]
sys.path.insert(0, MAIN_PATH)

CPU times: user 1.94 s, sys: 3.55 s, total: 5.49 s
Wall time: 837 ms


In [2]:
# Run a Federated Learning experiment
from data_loader.mnist import MnistDatasetManager
from models.mnist_model import MnistFullConnectModel, SimpleCNN, EfficientCNN
from server.base_server import BaseServer
from client.base_client import BaseClient
from experiments.base_experiment import BaseExperiment
from gradients.noise import GaussianNoiseGenerator, NoNoiseGenerator,StaircaseNoiseGenerator
from metrics.classification import multiclass_accuracy

In [7]:
class DemoMnistExperiment(BaseExperiment):
    def __init__(self, 
                 client_num: int = 2, 
                 lr: float=0.01, 
                 noise_generator=None,
                 max_norm = 3,
                 sampling_rate=0.01):
        if noise_generator is None:
            noise_generator = NoNoiseGenerator()
        self.noise_generator = noise_generator
        self.lr = lr
        self.max_norm = max_norm
        self.sampling_rate = sampling_rate
        self.client_num = client_num
        self._init_server_clients(client_num, self.lr)
        self._init_data(client_num)

    def _init_server_clients(self, client_num, lr):
        model = EfficientCNN
        self.clients = [BaseClient(model(lr=lr), 
                                   client_id=idx, 
                                   noise_generator=self.noise_generator)
                        for idx in range(client_num)]
        self.server = BaseServer(model(lr=lr, 
                                       max_norm=self.max_norm))

    def _init_data(self, client_num):
        data_manager = MnistDatasetManager(n_parties=client_num, 
                                           sampling_lot_rate=self.sampling_rate)
        self.client_train_datas = data_manager.train_loaders
        self.valid_datas = data_manager.validation_loader
        self.test_data = data_manager.test_loader

    def evaluate_model(self, data):
        total_correct = 0
        total_sample_num = 0
        with torch.no_grad():
            for _, (inputs, target) in enumerate(data):
                predict_labels = self.server.predict(inputs)
                correct, sample_num = multiclass_accuracy(y_pred=predict_labels, 
                                                          y_true=target)
                total_correct += correct
                total_sample_num += sample_num
                
        return total_correct / total_sample_num
        
    def get_validation_result(self):
        return self.evaluate_model(self.valid_datas)
    
    def get_test_result(self):
        return self.evaluate_model(self.test_data)
    
    def aggeragate(self, clients):
        self.server.aggeragate_model(clients)
    # def aggeragate(self):
    #     self.server.aggeragate_model(self.clients)
    def run(self, epochs: int, client_epochs: int):
        self._init_data(self.client_num)
        for client in self.clients:
            client.set_training_mode(for_gradient=False)

        for epoch in range(epochs):
            print(self.get_validation_result())
            selected_clients=[]
            for i, (client, client_train_data) in enumerate(self.shuffled_data(to_shuffle=True)):
                # client_train_data is a generator of dataloders
                if i == 10:
                    break
                client.train(client_train_data, client_epochs=client_epochs)
                selected_clients.append(client)

            self.aggeragate(selected_clients)

            self.distribute_model()



In [8]:
EXPERIMENT = DemoMnistExperiment(client_num=9, 
                                 lr = 0.01, 
                                 max_norm=0.1,
                                 sampling_rate=0.05,
                                 noise_generator=NoNoiseGenerator(),
                                )
EXPERIMENT.run(epochs=100, client_epochs=2)

0.04683333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333
0.11283333333333333


KeyboardInterrupt: 

In [ ]:
EXPERIMENT = DemoMnistExperiment(client_num=2, 
                                 lr = 0.01, 
                                 max_norm=0.1,
                                 sampling_rate=0.05,
                                 noise_generator=GaussianNoiseGenerator(sensitivity=0.703),
                                )
EXPERIMENT.run(epochs=100, client_epochs=2)

In [ ]:
EXPERIMENT = DemoMnistExperiment(client_num=5, 
                                 lr = 0.01, 
                                 max_norm=10,
                                 sampling_rate=0.05,6
                                 noise_generator=GaussianNoiseGenerator(sensitivity=0.385))
EXPERIMENT.run(30)

In [ ]:
EXPERIMENT = DemoMnistExperiment(client_num=5, 
                                 lr = 0.01, 
                                 max_norm=0.1,
                                 sampling_rate=0.05,
                                 noise_generator=GaussianNoiseGenerator(sensitivity=1.362926))
EXPERIMENT.run(30)

In [ ]:
EXPERIMENT = DemoMnistExperiment(client_num=5, 
                                 lr = 0.01, 
                                 max_norm=0.1,
                                 sampling_rate=0.05,
                                 noise_generator=GaussianNoiseGenerator(sensitivity=1.362926))
EXPERIMENT.run(30)

In [ ]:
EXPERIMENT = DemoMnistExperiment(client_num=5, 
                                 lr = 0.01, 
                                 max_norm=0.1,
                                 sampling_rate=0.05,
                                 noise_generator=GaussianNoiseGenerator(sensitivity=1.362926))
EXPERIMENT.run(30)

In [ ]:
EXPERIMENT = DemoMnistExperiment(client_num=1, 
                                 lr = 0.001, 
                                 noise_generator=NoNoiseGenerator())

In [ ]:
EXPERIMENT.run(10)

0.1165
<bound method Module.parameters of SimpleCNN(
  (conv1): Conv2d(1, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (relu): ReLU()
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (fc1): Linear(in_features=3136, out_features=128, bias=True)
  (fc2): Linear(in_features=128, out_features=10, bias=True)
  (loss_fn): CrossEntropyLoss()
)>
<bound method Module.parameters of SimpleCNN(
  (conv1): Conv2d(1, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (relu): ReLU()
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (fc1): Linear(in_features=3136, out_features=128, bias=True)
  (fc2): Linear(in_features=128, out_features=10, bias=True)
  (loss_fn): CrossEntropyLoss()
)>
<bound method Module.parameters of SimpleCNN(
  (conv1): Conv2d(1, 32, ke